# Load and prepare models for assemblage into a community

In [2]:
# define the environment path 
from pprint import pprint
import os
local_cobrakbase_path = os.path.join('C:', 'Users', 'Andrew Freiburger','Documents','Argonne','cobrakbase')
os.environ["HOME"] = local_cobrakbase_path

# import the models
import cobrakbase
token = 'CKYZK6AZ5V2CT5ILYP7JAXFPW3OLT6VF'
kbase_api = cobrakbase.KBaseAPI(token)
model1 = kbase_api.get_from_ws("E_iAH991V2",40576)
model2 = kbase_api.get_from_ws("E_iML1515.kb",40576)
models = [model1, model2]
com_model = kbase_api.get_from_ws("CMM_iAH991V2_iML1515.kb",40576)

C:\Users\Andrew Freiburger\AppData\Local\Programs\Python\Python39\lib\site-packages\requests\__init__.py:102: RequestsDependencyWarning: urllib3 (1.26.9) or chardet (5.0.0)/charset_normalizer (2.0.12) doesn't match a supported version!
  warnings.warn("urllib3 ({}) or chardet ({})/charset_normalizer ({}) doesn't match a supported "


cobrakbase 0.2.8


ConnectionError: HTTPSConnectionPool(host='kbase.us', port=443): Max retries exceeded with url: /services/ws/ (Caused by NewConnectionError('<urllib3.connection.HTTPSConnection object at 0x0000024C25B698E0>: Failed to establish a new connection: [Errno 11001] getaddrinfo failed'))

### compatabilize models

In [2]:
# %run ../../../modelseedpy/community/mscompatibility.py

# # compatabilize the models
# mscompat = MSCompatibility(modelseed_db_path = os.path.join('..', '..', '..', '..', 'ModelSEEDDatabase'))
# models = mscompat.align_exchanges(models, conflicts_file_name='exchanges_conflicts.json', model_names = ["iML1515", "iSB1139.kb.gf"])
# models = mscompat.standardize(models, conflicts_file_name = 'standardized_exchange_metabolites.json', model_names = ["iML1515", "iSB1139.kb.gf"])

### build community

In [ ]:
%run ../../../modelseedpy/community/mscommunity.py

# construct the community models
com_model, indices = MSCommunity.build_from_species_models(models)

In [4]:
compartments = set()
for met in com_model.metabolites:
    compartments.add(met.compartment)
display(compartments)

{'b2', 'c0', 'c1', 'c2', 'e0', 'p1'}

In [7]:
for rxn in model1.reactions:
    if "bio" in rxn.id:
        print(rxn.id)
for rxn in model2.reactions:
    if "bio" in rxn.id:
        print("model 2", rxn.id)

bio3
bio2
model 2 bio4


In [5]:
print(com_model.optimize().objective_value)

0.0


# test the minimal media method

In [2]:
%run ../../../modelseedpy/community/mscommunity.py
comm_media = MSCommunity.minimal_community_media(models, com_model)

C:\Users\Andrew Freiburger\AppData\Local\Programs\Python\Python39\lib\site-packages\cobra\medium\minimal_medium.py:112: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
  medium = pd.Series()
C:\Users\Andrew Freiburger\AppData\Local\Programs\Python\Python39\lib\site-packages\cobra\medium\minimal_medium.py:112: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
  medium = pd.Series()


Initial media defined with 22 exchanges
Syntrophic fluxes examined after 0.0 minutes, with 2 change(s): {'values_changed': {"root['EX_cpd00009_e0']": {'new_value': 3.5778112627048535, 'old_value': 0.17640199999584474}, "root['EX_cpd10515_e0']": {'new_value': 5.228081150919393, 'old_value': 0.0009336000000000001}}}
The 5040 permutations of the {'EX_cpd10515_e0', 'EX_cpd00009_e0', 'EX_cpd00028_e0', 'EX_cpd03725_e0', 'EX_cpd00104_e0', 'EX_cpd00294_e0', 'EX_cpd00048_e0'} redundant compounds, from absolute tolerance of 1e-4, will be examined.
Unique combinations:
4 [{'EX_cpd10515_e0', 'EX_cpd00009_e0', 'EX_cpd00028_e0', 'EX_cpd00104_e0', 'EX_cpd00048_e0'}, {'EX_cpd10515_e0', 'EX_cpd00028_e0', 'EX_cpd00104_e0', 'EX_cpd00294_e0', 'EX_cpd00048_e0'}, {'EX_cpd00009_e0', 'EX_cpd00028_e0', 'EX_cpd03725_e0', 'EX_cpd00104_e0', 'EX_cpd00048_e0'}, {'EX_cpd00028_e0', 'EX_cpd03725_e0', 'EX_cpd00104_e0', 'EX_cpd00294_e0', 'EX_cpd00048_e0'}]


 10704


 10989


 3914


 4199
{'EX_cpd00007_e0': 1000.000022

In [19]:
final_permutations = [{'EX_cpd03725_e0', 'EX_cpd00541_e0', 'EX_cpd00104_e0', 'EX_cpd00048_e0', 'EX_cpd00028_e0', 'EX_cpd00009_e0'}, 
                      {'EX_cpd03725_e0', 'EX_cpd00541_e0', 'EX_cpd00104_e0', 'EX_cpd00048_e0', 'EX_cpd00028_e0', 'EX_cpd00294_e0'}, 
                      {'EX_cpd00541_e0', 'EX_cpd00104_e0', 'EX_cpd10515_e0', 'EX_cpd00048_e0', 'EX_cpd00028_e0', 'EX_cpd00009_e0'}, 
                      {'EX_cpd00541_e0', 'EX_cpd00104_e0', 'EX_cpd10515_e0', 'EX_cpd00048_e0', 'EX_cpd00028_e0', 'EX_cpd00294_e0'}]
possible_removal_tracker = {}
best = 0
for possible_removal in final_permutations:
    cpdID_sum = sum([int(cpd.split('_')[1].replace("cpd", "")) for cpd in possible_removal])
    if cpdID_sum > best:
        best = cpdID_sum
        possible_removal_tracker = {best:[possible_removal]}
    elif cpdID_sum == best:
        possible_removal_tracker[best].append(possible_removal) 
cpds_to_remove = list(possible_removal_tracker.values())[0][0]
for permutation in cpds_to_remove:
    media["community_media"].pop(cpd)

{'EX_cpd10515_e0', 'EX_cpd00541_e0', 'EX_cpd00048_e0', 'EX_cpd00028_e0', 'EX_cpd00104_e0', 'EX_cpd00294_e0'}


KeyError: 'EX_cpd00294_e0'

In [25]:
display(media["community_media"])
len(media["community_media"])

{'EX_cpd00149_e0': 0.0004692000000000001,
 'EX_cpd00254_e0': 0.0012921,
 'EX_cpd00205_e0': 0.0190358,
 'EX_cpd00007_e0': 474.04547837401856,
 'EX_cpd01017_e0': 331.2439003175204,
 'EX_cpd00034_e0': 0.0004992000000000001,
 'EX_cpd00098_e0': 0.00046680000000000007,
 'EX_cpd00166_e0': 0.0004891000000000001,
 'EX_cpd00971_e0': 0.00046679999999998945,
 'EX_cpd00009_e0': 3.3415759270153345,
 'EX_cpd00063_e0': 0.0009620000000000001,
 'EX_cpd00030_e0': 0.0005326,
 'EX_cpd11574_e0': 2.1000000000000002e-06,
 'EX_cpd00058_e0': 6.74000000568434e-05,
 'EX_cpd00244_e0': 3.07e-05,
 'EX_cpd00099_e0': 0.0004952,
 'EX_cpd03725_e0': 462.1310614102555}

17

In [29]:
from deepdiff import DeepDiff

dict1 = {"test":2, "test2":5}
dict2 = dict1.copy()
dict2.pop("test")
DeepDiff(dict1, dict2)

{'dictionary_item_removed': [root['test']]}

In [2]:
from modelseedpy.community.mscompatibility import MSCompatibility
from modelseedpy import FBAHelper
from time import process_time
from math import isclose
from itertools import combinations, permutations
from cobra.medium import minimal_medium
from deepdiff import DeepDiff
def estimate_minimal_community_media(models, com_model=None, syntrophy=True, min_growth=0.1, conserved_cpds=[]):
    # determine the unique combination of all species minimal media 
    # models = MSCompatibility.align_exchanges(models, True, "standardization_corrections.json")
    media = {}
    media["community_media"], media["members"] = {}, {}
    for model in models:
        media["members"][model.id] = {}
        with model:
            media["members"][model.id]["media"] = minimal_medium(model, min_growth, minimize_components=True).to_dict()
            model.medium = media["members"][model.id]["media"]
            media["members"][model.id]["solution"] = FBAHelper.solution_to_dict(model.optimize())
            media["community_media"] = FBAHelper.sum_dict(model.medium, media["community_media"])

    # subtract syntrophic interactions and remove satisfied fluxes
    org_media = media["community_media"].copy()
    original_time = process_time()
    print(f"Initial media defined with {len(media['community_media'])} exchanges")
    changed = 0
    if syntrophy:
        for model in models:
            for rxnID, flux in media["members"][model.id]["solution"].items():
                if rxnID in media["community_media"] and flux > 0:
                    stoich = list(model.reactions.get_by_id(rxnID).metabolites.values())[0]
                    media["community_media"][rxnID] -= flux*stoich
                    changed += 1
        media["community_media"] = {ID:flux for ID, flux in media["community_media"].items() if flux > 0}

    syntrophic_media = media["community_media"].copy()
    syntrophic_time = process_time()
    syntrophy_difference = DeepDiff(org_media, syntrophic_media)
    changed_quantity = len(list(syntrophy_difference.values())[0].values())
    print(f"Syntrophic fluxes examined after {(syntrophic_time-original_time)/60} minutes, with {changed_quantity} change(s):", syntrophy_difference)

    # JANGA method of further reduction
    changed = 0
    if com_model:
        community_model = com_model 
        ## identify additionally redundant compounds
        redundant_cpds = set()
        community_model.medium = syntrophic_media
        original_obj_value = com_model.optimize().objective_value
        for cpd in media["community_media"]:
            new_media = media["community_media"].copy()
            new_media.pop(cpd)
            community_model.medium = new_media
            sol = community_model.optimize()
            if isclose(sol.objective_value, original_obj_value, abs_tol=1e-4):
                redundant_cpds.add(cpd)

        ## vet the permutations
        permuts = [p for p in permutations(redundant_cpds)]
        print(f"The {len(permuts)} permutations of the {redundant_cpds} redundant compounds, from absolute tolerance of 1e-4, will be examined.")
        permutation_results = []
        best = 0
        failed_permutation_starts = []
        for perm_index, permut in enumerate(permuts):
            print(f"{perm_index}/{len(permuts)}", end="\r")
            permutation_segments = [permut[:index] for index in range(len(permut), 2, -1)]
            ### block previously discovered failures and successes, respectively
            if not any([seg in failed_permutation_starts for seg in permutation_segments]):
                if best < 3 or not any([set(permut[:best-1]) == set(success[:best-1]) for success in permutation_results]):
                    successful_removal = 0
                    new_media = media["community_media"].copy()
                    for cpd in permut:
                        ### parameterize and simulate the community
                        new_media.pop(cpd)
                        community_model.medium = new_media
                        sol = community_model.optimize()
                        if isclose(sol.objective_value, original_obj_value, abs_tol=1e-7):
                            successful_removal += 1
                            continue
                        # print("objective value discrepancy:", sol.objective_value, original_obj_value)
                        failed_permutation_starts.append(permut[:successful_removal+1])
                        break
                    if successful_removal >= best:
                        if successful_removal > best:
                            best = successful_removal
                            permutation_results = []
                        permut_set = set(permut[:best+1])  # slice only the elements that are removable
                        if permut_set not in permutation_results:
                            permutation_results.append(permut)

        ## filter to only the most minimal media
        solutions_paths, new_combinations = [], []
        for permut in permutation_results:
            start_removal_index =  best - len(permut) # the compound at which growth is lost
            removable_compounds = set(list(permut)[:start_removal_index])
            solutions_paths.append(removable_compounds)
            if removable_compounds not in new_combinations:
                new_combinations.append(removable_compounds)

        unique_combinations, unique_paths = [], []
        for removal_path in solutions_paths:
            path_permutations = permutations(removal_path)
            if all([set(path) in solutions_paths for path in path_permutations]):
                combination = combinations(removal_path, len(removal_path))
                if not all([set(com) in unique_combinations for com in combination]):
                    for com in combinations(removal_path, len(removal_path)):
                        unique_combinations.append((set(com)))
            else:
                if set(removal_path) not in unique_paths:
                    unique_paths.append((set(removal_path)))
        if unique_combinations[0]:
            print("Unique combinations:")
            print(len(unique_combinations), unique_combinations) 
            if len(unique_combinations) == 1:
                media["community_media"] = FBAHelper.remove_media_compounds(media["community_media"], unique_combinations[0])
        if unique_paths:
            print("Unique paths:")
            print(len(unique_paths), unique_paths)

        # further remove compounds from the media, while defaulting to the removal with the largest ID values
        possible_removal_tracker = {}
        possible_options = unique_combinations+unique_paths
        if conserved_cpds:
            possible_options = [opt for opt in possible_options if not any(cpd in conserved_cpds for cpd in opt)]
        best = 0
        for possible_removal in possible_options:
            cpdID_sum = sum([int(cpd.split('_')[1].replace("cpd", "")) for cpd in possible_removal])
            if cpdID_sum > best:
                best = cpdID_sum
                possible_removal_tracker = {best:[possible_removal]}
            elif cpdID_sum == best:
                possible_removal_tracker[best].append(possible_removal) 
        cpds_to_remove = list(possible_removal_tracker.values())[0][0]
        pprint(media["community_media"])
        for cpd in cpds_to_remove:
            media["community_media"].pop(cpd)

    jenga_media = media["community_media"].copy()
    jenga_time = process_time()
    jenga_difference = DeepDiff(syntrophic_media, jenga_media)
    return jenga_difference
    changed_quantity = sum(len(list(diff.values())[0]) for diff in jenga_difference.values)
    print(f"Jenga fluxes examined after {(jenga_time-syntrophic_time)/60} minutes, with {changed_quantity} change(s):", jenga_difference)
    return media

In [ ]:
# from modelseedpy.community.mscommunity import MSCommunity
# %run ../../../modelseedpy/community/mscommunity.py
# media = MSCommunity.estimate_minimal_community_media(models, com_model)

media = estimate_minimal_community_media(models, com_model)

# pprint(media)
# with open("community_media.json", 'w') as out:
#     dump(media, out, indent=3)

C:\Users\Andrew Freiburger\AppData\Local\Programs\Python\Python39\lib\site-packages\cobra\medium\minimal_medium.py:112: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
  medium = pd.Series()
C:\Users\Andrew Freiburger\AppData\Local\Programs\Python\Python39\lib\site-packages\cobra\medium\minimal_medium.py:112: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
  medium = pd.Series()


Initial media defined with 23 exchanges
Syntrophic fluxes examined after 0.0 minutes, with 2 change(s): {'values_changed': {"root['EX_cpd10515_e0']": {'new_value': 2.202171349414016, 'old_value': 0.0009336000000000001}, "root['EX_cpd00009_e0']": {'new_value': 3.4263830393007493, 'old_value': 0.1768688000053277}}}
The 3628800 permutations of the {'EX_cpd00028_e0', 'EX_cpd00037_e0', 'EX_cpd00104_e0', 'EX_cpd00009_e0', 'EX_cpd03725_e0', 'EX_cpd10515_e0', 'EX_cpd00048_e0', 'EX_cpd01017_e0', 'EX_cpd00007_e0', 'EX_cpd00541_e0'} redundant compounds, from absolute tolerance of 1e-4, will be examined.


In [ ]:
jenga_difference

In [1]:
import warnings
warnings.filterwarnings(action='once')

# define the environment path 
from pprint import pprint
from json import dump
import os
local_cobrakbase_path = os.path.join('C:', 'Users', 'Andrew Freiburger','Documents','Argonne','cobrakbase')
os.environ["HOME"] = local_cobrakbase_path

# import the models
import cobrakbase
token = 'RBP7R34IILI6IQN5533VVSVUZM6H7YU7'
kbase_api = cobrakbase.KBaseAPI(token)

model1 = kbase_api.get_from_ws("E_iAH991V2",40576)
model2 = kbase_api.get_from_ws("E_iML1515.kb",40576)
com_model = kbase_api.get_from_ws("CMM_iAH991V2_iML1515.kb",40576)
models = [model1, model2]

C:\Users\Andrew Freiburger\AppData\Local\Programs\Python\Python39\lib\site-packages\cobra\io\dict.py:71: DeprecationWarning: `np.float` is a deprecated alias for the builtin `float`. To silence this warning, use `float` by itself. Doing this will not modify any behavior and is safe. If you specifically wanted the numpy scalar type, use `np.float64` here.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  value: Union[str, np.float, np.bool, Set, Dict]
C:\Users\Andrew Freiburger\AppData\Local\Programs\Python\Python39\lib\site-packages\cobra\io\dict.py:71: DeprecationWarning: `np.bool` is a deprecated alias for the builtin `bool`. To silence this warning, use `bool` by itself. Doing this will not modify any behavior and is safe. If you specifically wanted the numpy scalar type, use `np.bool_` here.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecatio

cobrakbase 0.2.8


In [4]:
for model in models:
    for rxn in model.reactions:
        if len(rxn.metabolites) != len(rxn.reactants)+len(rxn.products):
            print(f"The {rxn.id} reaction is not at parity")

In [5]:
# from cobra.medium import minimal_medium
# minimal_media = {}
# for model in models:
#     minimal_media[model.id] = minimal_medium(model, minimize_components=True)
    
# # from pprint import pprint
# # pprint(minimal_media)
# def sum_dict(d1,d2):
#     for key, value in d1.items():
#         if key in d2:
#             d2[key] += value
#         else:
#             d2[key] = value
#     return d2

# com_media = {}
# for media in minimal_media.values():
#     com_media = sum_dict(media, com_media)
# print(len(com_media.keys()), com_media)

C:\Users\Andrew Freiburger\AppData\Local\Programs\Python\Python39\lib\site-packages\cobra\medium\boundary_types.py:60: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
  matches = pd.Series(
C:\Users\Andrew Freiburger\AppData\Local\Programs\Python\Python39\lib\site-packages\cobra\medium\boundary_types.py:60: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
  matches = pd.Series(
C:\Users\Andrew Freiburger\AppData\Local\Programs\Python\Python39\lib\site-packages\cobra\medium\minimal_medium.py:112: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
  medium = pd.Series()
C:\Users\Andrew Freiburger\AppData\Local\Programs\Python\Python39\lib\site-packages\cobra\

### validate the minimal community media via the Jenga method

In [3]:
com_model.medium = media["community_media"]
original_obj_value = com_model.optimize().objective_value
print(original_obj_value)
print(len(media["community_media"]), media["community_media"])

0.1999999999999993
22 {'EX_cpd00149_e0': 0.0004693000000265238, 'EX_cpd00205_e0': 0.019986099999982798, 'EX_cpd10515_e0': 0.9291150603766285, 'EX_cpd00034_e0': 0.0005009000000265238, 'EX_cpd00009_e0': 1.5942658971694015, 'EX_cpd00028_e0': 0.0004668000000265238, 'EX_cpd00063_e0': 0.0009873000000197862, 'EX_cpd00166_e0': 0.0004668000000265238, 'EX_cpd00254_e0': 0.0013343000000531902, 'EX_cpd01017_e0': 762.3258667404602, 'EX_cpd00007_e0': 1000, 'EX_cpd00971_e0': 0.0004668000000265238, 'EX_cpd00098_e0': 0.0004668000000265238, 'EX_cpd00030_e0': 0.0005359000000265238, 'EX_cpd00104_e0': 2e-07, 'EX_cpd03725_e0': 756.2477963726411, 'EX_cpd03701_e0': 706.3462082535365, 'EX_cpd00048_e0': 0.02518159999999625, 'EX_cpd00058_e0': 7.09e-05, 'EX_cpd11574_e0': 7.000000000000001e-07, 'EX_cpd00099_e0': 0.0005204999999932625, 'EX_cpd00244_e0': 3.23e-05}


In [12]:
from itertools import permutations
from math import isclose

# identify additionally redundant compounds
redundnant_cpds = set()
community_model = com_model
for cpd in media["community_media"]:
    new_media = media["community_media"].copy()
    new_media.pop(cpd)
    community_model.medium = new_media
    sol = community_model.optimize()
    if isclose(sol.objective_value, original_obj_value, abs_tol=1e-4):
        print("redundant cpd:", cpd)
        redundnant_cpds.add(cpd)
        
# vet the permutations
permuts = [p for p in permutations(redundnant_cpds)]
print(f"The {len(permuts)} permutations of the {redundnant_cpds} redundant compounds will be examined.")
permutation_results = {}
best = 0
failed_permutation_starts = []
for perm_index, permut in enumerate(permuts):
    print(f"{perm_index}/{len(permuts)}", end="\r")
    permutation_segments = [permut[:index] for index in range(len(permut), 2, -1)]
    ### block previously discovered failures and successes, respectively
    if not any([seg in failed_permutation_starts for seg in permutation_segments]):
        if best < 2 or not any([set(permut[:best-1]) == set(success[:best-1]) for success in permutation_results]):
            successful_removal = 0
            new_media = media["community_media"].copy()
            for cpd in permut:
                ### parameterize and simulate the community
                new_media.pop(cpd)
                community_model.medium = new_media
                sol = community_model.optimize()
                if isclose(sol.objective_value, original_obj_value, abs_tol=1e-7):
                    successful_removal += 1
                    continue
                # print("objective value discrepancy:", sol.objective_value, original_obj_value)
                failed_permutation_starts.append(permut[:successful_removal+1])
                break
            if successful_removal >= best:
                if successful_removal > best:
                    best = successful_removal
                    permutation_results = {}
                permutation_results[permut] = successful_removal

print(len(permutation_results))
pprint(permutation_results)

redundant cpd: EX_cpd10515_e0
redundant cpd: EX_cpd00009_e0
redundant cpd: EX_cpd00028_e0
redundant cpd: EX_cpd00007_e0
redundant cpd: EX_cpd00104_e0
redundant cpd: EX_cpd03725_e0
redundant cpd: EX_cpd03701_e0
redundant cpd: EX_cpd00048_e0
The 40320 permutations of the {'EX_cpd00028_e0', 'EX_cpd00104_e0', 'EX_cpd03725_e0', 'EX_cpd10515_e0', 'EX_cpd00009_e0', 'EX_cpd00048_e0', 'EX_cpd00007_e0', 'EX_cpd03701_e0'} redundant compounds will be examined.
23319/40320
{('EX_cpd00028_e0', 'EX_cpd00007_e0', 'EX_cpd00104_e0', 'EX_cpd03701_e0', 'EX_cpd10515_e0', 'EX_cpd03725_e0', 'EX_cpd00009_e0', 'EX_cpd00048_e0'): 5,
 ('EX_cpd00028_e0', 'EX_cpd00007_e0', 'EX_cpd00104_e0', 'EX_cpd10515_e0', 'EX_cpd00009_e0', 'EX_cpd03725_e0', 'EX_cpd00048_e0', 'EX_cpd03701_e0'): 5,
 ('EX_cpd00028_e0', 'EX_cpd00007_e0', 'EX_cpd10515_e0', 'EX_cpd03701_e0', 'EX_cpd00104_e0', 'EX_cpd03725_e0', 'EX_cpd00009_e0', 'EX_cpd00048_e0'): 5,
 ('EX_cpd00028_e0', 'EX_cpd00009_e0', 'EX_cpd00007_e0', 'EX_cpd00104_e0', 'EX_cpd1051

In [13]:
print(len(permutation_results))
pprint(permutation_results)

23
{('EX_cpd00028_e0', 'EX_cpd00007_e0', 'EX_cpd00104_e0', 'EX_cpd03701_e0', 'EX_cpd10515_e0', 'EX_cpd03725_e0', 'EX_cpd00009_e0', 'EX_cpd00048_e0'): 5,
 ('EX_cpd00028_e0', 'EX_cpd00007_e0', 'EX_cpd00104_e0', 'EX_cpd10515_e0', 'EX_cpd00009_e0', 'EX_cpd03725_e0', 'EX_cpd00048_e0', 'EX_cpd03701_e0'): 5,
 ('EX_cpd00028_e0', 'EX_cpd00007_e0', 'EX_cpd10515_e0', 'EX_cpd03701_e0', 'EX_cpd00104_e0', 'EX_cpd03725_e0', 'EX_cpd00009_e0', 'EX_cpd00048_e0'): 5,
 ('EX_cpd00028_e0', 'EX_cpd00009_e0', 'EX_cpd00007_e0', 'EX_cpd00104_e0', 'EX_cpd10515_e0', 'EX_cpd03725_e0', 'EX_cpd00048_e0', 'EX_cpd03701_e0'): 5,
 ('EX_cpd00028_e0', 'EX_cpd00009_e0', 'EX_cpd00007_e0', 'EX_cpd10515_e0', 'EX_cpd00104_e0', 'EX_cpd03725_e0', 'EX_cpd00048_e0', 'EX_cpd03701_e0'): 5,
 ('EX_cpd00028_e0', 'EX_cpd00009_e0', 'EX_cpd00048_e0', 'EX_cpd00104_e0', 'EX_cpd03725_e0', 'EX_cpd10515_e0', 'EX_cpd00007_e0', 'EX_cpd03701_e0'): 5,
 ('EX_cpd00028_e0', 'EX_cpd00009_e0', 'EX_cpd00048_e0', 'EX_cpd03725_e0', 'EX_cpd00104_e0', 'EX_c

In [11]:
# orig_permutation_results = permutation_results
print(len(orig_permutation_results))
pprint(orig_permutation_results)

1211
{('EX_cpd00007_e0', 'EX_cpd00028_e0', 'EX_cpd00009_e0', 'EX_cpd00104_e0', 'EX_cpd10515_e0', 'EX_cpd00048_e0', 'EX_cpd03725_e0', 'EX_cpd03701_e0'): 5,
 ('EX_cpd00007_e0', 'EX_cpd00028_e0', 'EX_cpd00009_e0', 'EX_cpd00104_e0', 'EX_cpd10515_e0', 'EX_cpd03701_e0', 'EX_cpd03725_e0', 'EX_cpd00048_e0'): 5,
 ('EX_cpd00007_e0', 'EX_cpd00028_e0', 'EX_cpd00009_e0', 'EX_cpd00104_e0', 'EX_cpd10515_e0', 'EX_cpd03725_e0', 'EX_cpd00048_e0', 'EX_cpd03701_e0'): 5,
 ('EX_cpd00007_e0', 'EX_cpd00028_e0', 'EX_cpd00009_e0', 'EX_cpd10515_e0', 'EX_cpd00104_e0', 'EX_cpd00048_e0', 'EX_cpd03725_e0', 'EX_cpd03701_e0'): 5,
 ('EX_cpd00007_e0', 'EX_cpd00028_e0', 'EX_cpd00009_e0', 'EX_cpd10515_e0', 'EX_cpd00104_e0', 'EX_cpd03701_e0', 'EX_cpd03725_e0', 'EX_cpd00048_e0'): 5,
 ('EX_cpd00007_e0', 'EX_cpd00028_e0', 'EX_cpd00009_e0', 'EX_cpd10515_e0', 'EX_cpd00104_e0', 'EX_cpd03725_e0', 'EX_cpd00048_e0', 'EX_cpd03701_e0'): 5,
 ('EX_cpd00007_e0', 'EX_cpd00028_e0', 'EX_cpd00104_e0', 'EX_cpd00009_e0', 'EX_cpd10515_e0', 'EX

# Verify the similitude of the new method that omits combinationally identical permutations

In [27]:
# from itertools import combinations
from deepdiff import DeepDiff
org_permut_combinations = []
for org_permut, removed in permutation_results.items():
    permut_set = set(org_permut[:removed+1])
    if permut_set not in org_permut_combinations:
        org_permut_combinations.append(permut_set)
    
new_permut_combinations = []
for new_permut, removed in permutation_results.items():
    permut_set = set(new_permut[:removed+1])
    if permut_set not in new_permut_combinations:
        new_permut_combinations.append(permut_set)
    
if not DeepDiff(org_permut_combinations, new_permut_combinations):
    print("Method parity")
# pprint(org_permut_combinations)
# pprint(new_permut_combinations)

Method parity


In [8]:
from itertools import permutations
from math import isclose

# identify additionally redundant compounds
redundnant_cpds = set()
community_model = com_model
for cpd in media["community_media"]:
    new_media = media["community_media"].copy()
    new_media.pop(cpd)
    community_model.medium = new_media
    sol = community_model.optimize()
    if isclose(sol.objective_value, original_obj_value, abs_tol=1e-4):
        # print("redundant cpd:", cpd)
        redundnant_cpds.add(cpd)
        
# vet the permutations
permuts = [p for p in permutations(redundnant_cpds)]
print(f"The {len(permuts)} permutations of the {redundnant_cpds} redundant compounds will be examined.")
permutation_results = {}
best = 0
failed_permutation_starts = []
for perm_index, permut in enumerate(permuts):
    print(f"{perm_index}/len(permuts)", end="\r")
    permutation_segments = [p[:index] for index in range(len(permut), 2, -1)]
    if not any(seg in failed_permutation_starts for seg in permutation_segments):
        successful_removal = 0
        new_media = media["community_media"].copy()
        for cpd in permut:
            ### parameterize and simulate the community
            new_media.pop(cpd)
            community_model.medium = new_media
            sol = community_model.optimize()
            if isclose(sol.objective_value, original_obj_value, abs_tol=1e-7):
                successful_removal += 1
                continue
            # print("objective value discrepancy:", sol.objective_value, original_obj_value)
            failed_permutation_starts.append(permut[:successful_removal+1])
            break
        if successful_removal >= best:
            if successful_removal > best:
                best = successful_removal
                permutation_results = {}
            permutation_results[permut] = successful_removal
                
pprint(permutation_results)

{'EX_cpd00009_e0', 'EX_cpd00048_e0', 'EX_cpd03725_e0', 'EX_cpd01570_e0', 'EX_cpd10515_e0', 'EX_cpd00541_e0', 'EX_cpd00028_e0', 'EX_cpd00104_e0'} 40320
{('EX_cpd00009_e0', 'EX_cpd00028_e0', 'EX_cpd00048_e0', 'EX_cpd00104_e0', 'EX_cpd00541_e0', 'EX_cpd01570_e0', 'EX_cpd03725_e0', 'EX_cpd10515_e0'): 5,
 ('EX_cpd00009_e0', 'EX_cpd00028_e0', 'EX_cpd00048_e0', 'EX_cpd00104_e0', 'EX_cpd00541_e0', 'EX_cpd01570_e0', 'EX_cpd10515_e0', 'EX_cpd03725_e0'): 5,
 ('EX_cpd00009_e0', 'EX_cpd00028_e0', 'EX_cpd00048_e0', 'EX_cpd00104_e0', 'EX_cpd00541_e0', 'EX_cpd03725_e0', 'EX_cpd01570_e0', 'EX_cpd10515_e0'): 6,
 ('EX_cpd00009_e0', 'EX_cpd00028_e0', 'EX_cpd00048_e0', 'EX_cpd00104_e0', 'EX_cpd00541_e0', 'EX_cpd03725_e0', 'EX_cpd10515_e0', 'EX_cpd01570_e0'): 6,
 ('EX_cpd00009_e0', 'EX_cpd00028_e0', 'EX_cpd00048_e0', 'EX_cpd00104_e0', 'EX_cpd00541_e0', 'EX_cpd10515_e0', 'EX_cpd01570_e0', 'EX_cpd03725_e0'): 6,
 ('EX_cpd00009_e0', 'EX_cpd00028_e0', 'EX_cpd00048_e0', 'EX_cpd00104_e0', 'EX_cpd00541_e0', 'EX_cpd

In [ ]:
from itertools import permutations, combinations

max_redundancy = max(list(permutation_results.values()))
top_redundancies = {k:v for k,v in permutation_results.items() if v==max_redundancy}
solutions_paths = []
new_combinations = []
for permut in top_redundancies:
    num_mets = len(permut)
    start_removal_index =  max_redundancy - num_mets
    removable_compounds = set(list(permut)[:start_removal_index])
    solutions_paths.append(removable_compounds)
    if removable_compounds not in new_combinations:
        new_combinations.append(removable_compounds)
    
print("Solutions path:")
print(len(solutions_paths), solutions_paths, "\n\n")

unique_combinations = []
unique_paths = []
for removal_path in solutions_paths:
    path_permutations = permutations(removal_path)
    if all([set(path) in solutions_paths for path in path_permutations]):
        combination = combinations(removal_path, len(removal_path))
        if not all([set(com) in unique_combinations for com in combination]):
            for com in combinations(removal_path, len(removal_path)):
                unique_combinations.append((set(com)))
    else:
        if not set(removal_path) in unique_paths:
            unique_paths.append((set(removal_path)))
        
print("Unique combinations:")
print(len(unique_combinations), unique_combinations) 
print("Unique paths:")
print(len(unique_paths), unique_paths)

# NOTE: The redundancies reveal that either EX_cpd00007_e0 or EX_cpd00048_e0 must be present, presumably as an electron source.

In [ ]:
com_media = media["community_media"].copy()
for cpd in media["community_media"]:
    if cpd in combinations[1]:
        com_media.pop(cpd)
print(len(com_media), com_media)
com_model.medium = com_media
print(com_model.optimize())

In [4]:
## identify additionally redundant compounds
redundnant_cpds = set()
original_obj_value = com_model.optimize().objective_value
community_model = com_model
for cpd in media["community_media"]:
    new_media = media["community_media"].copy()
    new_media.pop(cpd)
    community_model.medium = new_media
    sol = community_model.optimize()
    if isclose(sol.objective_value, original_obj_value, abs_tol=1e-7):
        print("redundant cpd:", cpd)
        redundnant_cpds.add(cpd)

## vet the permutations
permuts = permutations(redundnant_cpds)
permutation_results = {}
for permut in permuts:
    successful_removal = 0
    new_media = media["community_media"].copy()
    for cpd in permut:
        ### parameterize and simulate the community
        new_media.pop(cpd)
        community_model.medium = new_media
        sol = community_model.optimize()
        if isclose(sol.objective_value, original_obj_value, abs_tol=1e-7):
            successful_removal += 1
            continue
        print("objective value discrepancy:", sol.objective_value, original_obj_value)
        break
    permutation_results[permut] = successful_removal

## filter to only the most minimal media
max_redundancy = max(list(permutation_results.values()))
top_redundancies = {k:v for k,v in permutation_results.items() if v==max_redundancy}
solutions_paths, new_combinations = [], []
for permut in top_redundancies:
    start_removal_index =  max_redundancy - len(permut) # the compound at which growth is lost
    removable_compounds = set(list(permut)[:start_removal_index])
    solutions_paths.append(removable_compounds)
    if removable_compounds not in new_combinations:
        new_combinations.append(removable_compounds)

unique_combinations, unique_paths = [], []
for removal_path in solutions_paths:
    path_permutations = permutations(removal_path)
    if all([set(path) in solutions_paths for path in path_permutations]):
        combination = combinations(removal_path, len(removal_path))
        if not all([set(com) in unique_combinations for com in combination]):
            for com in combinations(removal_path, len(removal_path)):
                unique_combinations.append((set(com)))
    else:
        if set(removal_path) not in unique_paths:
            unique_paths.append((set(removal_path)))

C:\Users\Andrew Freiburger\AppData\Local\Programs\Python\Python39\lib\site-packages\cobra\medium\boundary_types.py:60: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
  matches = pd.Series(


NameError: name 'isclose' is not defined

In [2]:
for model in models:
    for rxn in media["community_media"]:
        cpd = rxn.removeprefix("EX_")
        if cpd in model.metabolites:
            for met_rxn in model.metabolites.get_by_id(cpd).reactions:
                print(met_rxn)
                print(model.reactions.get_by_id(rxn).metabolites.values()[0])
                break

NameError: name 'media' is not defined

In [2]:
from deepdiff import DeepDiff
unsynergized_media = MSCommunity.estimate_minimal_community_media(models, syntrophy=False)
diff = DeepDiff(unsynergized_media["community_media"], media["community_media"])
# refined_com_media = com_media.drop(com_media.loc[com_media.gt(0)])
# print(refined_com_media)
print(dir(diff))

C:\Users\Andrew Freiburger\AppData\Local\Programs\Python\Python39\lib\site-packages\cobra\medium\minimal_medium.py:112: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
  medium = pd.Series()
C:\Users\Andrew Freiburger\AppData\Local\Programs\Python\Python39\lib\site-packages\cobra\medium\minimal_medium.py:112: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
  medium = pd.Series()


Initial media defined with 24 exchanges
Syntrophic fluxes examined after 0.0 minutes
Syntrophic fluxes examined after -12.952864583333334 minutes
['CACHE_AUTO_ADJUST_THRESHOLD', '_DistanceMixin__calculate_item_deephash', '_DistanceMixin__get_item_rough_length', '__class__', '__class_getitem__', '__contains__', '__delattr__', '__delitem__', '__dict__', '__dir__', '__doc__', '__eq__', '__format__', '__ge__', '__getattribute__', '__getitem__', '__gt__', '__hash__', '__init__', '__init_subclass__', '__ior__', '__iter__', '__le__', '__len__', '__lt__', '__module__', '__ne__', '__new__', '__or__', '__reduce__', '__reduce_ex__', '__repr__', '__reversed__', '__ror__', '__setattr__', '__setitem__', '__sizeof__', '__str__', '__subclasshook__', '__weakref__', '_add_hash', '_auto_off_cache', '_auto_tune_cache', '_compare_in_order', '_count_diff', '_create_hashtable', '_dict_from_slots', '_diff', '_diff_booleans', '_diff_datetimes', '_diff_dict', '_diff_iterable', '_diff_iterable_in_order', '_diff_

In [1]:
models

NameError: name 'models' is not defined

In [11]:
from pprint import pprint
# pprint(diff.to_dict().values())
for key, value in diff.items():
    for met, change in value.items():
        print(met, change)

root['EX_cpd00009_e0'] {'new_value': 3.7260653229411527, 'old_value': 0.17640200000755446}
root['EX_cpd10515_e0'] {'new_value': 4.810363862531745, 'old_value': 0.0009336000000000001}
root['EX_cpd00971_e0'] {'new_value': 0.00046680000002653657, 'old_value': 0.0004668000000265238}


In [ ]:
from math import isclose
redundnant_cpds, partially_redundant = set(), set()
for cpd in media["community_media"]:
    new_media = media["community_media"].copy()
    new_media.pop(cpd)
    community_model = com_model
    community_model.medium = new_media
    sol = community_model.optimize()
    if isclose(sol.objective_value, original_obj_value, abs_tol=1e-7):
        print("redundant cpd:", cpd, "objective value difference:", sol.objective_value, original_obj_value)
        redundnant_cpds.add(cpd)
    elif sol.objective_value > original_obj_value:
        print("restraining cpd:", cpd, "\nobjective value:", sol.objective_value)
    elif not isclose(sol.objective_value, 0, abs_tol=1e-7):
        partially_redundant.add(cpd)
        print("partially redundant", cpd, "\nobjective value:", sol.objective_value)
if not redundnant_cpds:
    print("The media is minimal.")